In [1]:
using Calculus
using QuantEcon
import QuantEcon.simulate

In [2]:
#Model parameters
β = 0.9
ψ = 0.69
Π = [0.5 0.5;0.5 0.5]
G = [0.1;0.2]
θ = [1.0;1.0]
S = length(G)
A = eye(S)
for s = 1:S
    for sp = 1:S
        if ~(s == sp)
            A[s,sp] = -β*Π[s,sp]
        else
            A[s,sp] = 1.-β*Π[s,sp]
        end
    end
end

parameters = (β,ψ,Π,G,θ,S,A)

(0.9, 0.69, [0.5 0.5; 0.5 0.5], [0.1, 0.2], [1.0, 1.0], 2, [0.55 -0.45; -0.45 0.55])

In [3]:
function find_FB(parameters,maxn = 50, tol = 1e-6)
    β,ψ,Π,G,θ,S,A = parameters
            
    z = 0.5*ones(2*S) #c and n
    xi = zeros(S)
    res = zeros(2*S)
    dres = zeros(2*S,2*S)
    for i = 1:maxn
        c = z[1:S]
        n = z[S+1:2*S]
        for s = 1:S
            uc = 1.0/c[s]
            un = -ψ/(1. -n[s])
            ucc = -c[s]^(-2)
            unn = -ψ/(1. -n[s])^2
            
            ##residual
            res[s] = un + uc
            res[s+2] = n[s] - c[s] - G[s]
            
            ##jacobian
            dres[s,s] = ucc
            dres[s,s+S] = unn
            dres[S+s,s] = -1.
            dres[S+s,S+s] = 1.
        end
        step = -dres \ res
        z += step
        if norm(step)<tol
            break
        end
    end
    
    c = z[1:S]
    n = z[S+1:2*S]
    
    for s =1:S
        xi[s] = 1./c[s]
    end
    
    return [c;n;xi] 
end

find_FB (generic function with 3 methods)

In [4]:
function time1_allocation(μ,parameters=parameters,maxn = 50, tol = 1e-6)
    β,ψ,Π,G,θ,S,A = parameters
    
    z = find_FB(parameters)
    
    dres = zeros(3*S,3*S)
    res = zeros(3*S)
    for i = 1:20
        c = z[1:S]
        n = z[S+1:2*S]
        xi = z[2*S+1:3*S]
        for s = 1:S
            uc = 1.0/c[s]
            un = -ψ/(1. -n[s])
            ucc = -c[s]^(-2)
            uccc = 2.*c[s]^(-3)
            unn = -ψ/(1. -n[s])^2
            unnn = -2.*ψ/(1. -n[s])^3
            
            ##Residual
            res[s] = uc - μ*(ucc*c[s] + uc) - xi[s]
            res[S+s] = un - μ*(unn*n[s] + un) + xi[s]
            res[2*S+s] = n[s] - c[s] - G[s]
            
            ##Jacobian
            #first equations
            dres[s,s] = ucc - μ*(uccc*c[s] + ucc + ucc)
            dres[s,S+s] = 0.0
            dres[s,2*S+s] = -1.0
            #second equations
            dres[S+s,s] = 0.0 
            dres[S+s,S+s] = unn - μ*(unnn*n[s] + unn + unn)
            dres[S+s,2*S+s] = 1.0
            #third equations
            dres[2*S+s,s] = -1.0
            dres[2*S+s,S+s] = 1.0
            dres[2*S+s,2*S+s] = 0.0
        end
        step = -dres \ res
        z +=  step
        residual = norm(step)
        #println("residual at iteration ",i,": ",residual)
        if residual<tol
            break
        end
    end
        
    c = z[1:S]
    n = z[S+1:2*S]
    xi = z[2*S+1:3*S]
    
    uc = 1.0 ./ c
    un = -ψ ./(1. .- n)
    LHS = uc.*c + un.*n
    x = A \ LHS
    
    
    return c,n,x,xi
end                    

time1_allocation (generic function with 4 methods)

In [5]:
function time0_allocation(b_,s0,parameters=parameters,maxn = 5000, tol = 1e-5)
    β,ψ,Π,G,θ,S,A = parameters
    
    #Get FB
    FB = find_FB(parameters)
    c_FB = FB[1:S]
    n_FB = FB[S+1:2*S]
    xi_FB = FB[2*S+1:3*S]
    
    #Initial guess from FB
    z = [0.0;c_FB[1];n_FB[1];xi_FB[1]]
    
    dres = zeros(4,4)
    res = zeros(4)
    for i = 1:maxn
        μ,c0,n0,xi0 = z[1],z[2],z[3],z[4]
        xp = time1_allocation(μ)[3]
        uc0 = 1.0/c0
        un0 = -ψ/(1.0 - n0)
        ucc0 = -c0^(-2.)
        uccc0 = 2.0*c0^(-3.)
        unn0 = -ψ/(1.0 - n0)^2.
        unnn0 = -2.*ψ/(1.0 - n0)^3.

        ##Residual
        res[1] = uc0*(c0-b_) + un0*n0 + β*dot(Π[s0,:],xp)
        res[2] = uc0 - μ*(ucc0*(c0-b_) + uc0) - xi0
        res[3] = un0 - μ*(unn0*n0 + un0) + xi0
        res[4] = n0 - c0 - G[s0]

        ##Jacobian
        #first equation
        dres[1,1],dres[1,2] = 0.0, ucc0*(c0-b_) + uc0
        dres[1,3],dres[1,4] = unn0*n0 + un0, 0.0  
        #second equation       
        dres[2,1],dres[2,2] = -(ucc0*(c0-b_) + uc0), ucc0 - μ*(uccc0*(c0-b_) + ucc0 + ucc0)  
        dres[2,3],dres[2,4] = 0.0, -1.0
        #third equation       
        dres[3,1],dres[3,2] = -(unn0*n0 + un0), 0.0
        dres[3,3],dres[3,4] = unn0 - μ*(unnn0*n0 + unn0 + unn0), 1.0
        #fourth equation        
        dres[4,1],dres[4,2] = 0.0, -1.0 
        dres[4,3],dres[4,4] = 1.0, 0.0  
        
        #newton step
        step = -dres \ res
        
        #update
        z  +=  1/100*step
        residual = norm(step)
        println(residual)
        if residual<tol
            println("Converged in ",i," steps")
            break
        end
    end
    
    z
end

time0_allocation (generic function with 4 methods)

In [6]:
function time1_value(μ,parameters = parameters)
    β,ψ,Π,G,θ,S,A = parameters
    
    c,n,x,xi = time1_allocation(μ)
    u = log.(c) + ψ*log.(1.0-n)
    V = A\u
    
    c,n,x,V
end 

time1_value (generic function with 2 methods)

In [7]:
function Tau(c,n,parameters = parameters)
    β,ψ,Π,G,θ,S,A = parameters
    uc,un = 1.0 /c, -ψ /(1.0 - n)
    
    return 1.0 + un/uc
end

Tau (generic function with 2 methods)

In [8]:
function simulation(b_,s0,T,sHist,parameters=parameters)
    β,ψ,Π,G,θ,S,A = parameters
    
    if sHist == []
        mc = MarkovChain(Π, [1, 2])
        sHist = simulate(mc,T,init=1)
    end
    
    cHist,nHist = zeros(T+1),zeros(T+1)
    BHist,TauHist,μHist = zeros(T+1),zeros(T+1),zeros(T+1)
    
    #time0
    μ,c0,n0,_ = time0_allocation(b_,s0)
    cHist[1],nHist[1] = c0,n0 
    TauHist[1] = Tau(c0,n0)
    BHist[1] = b_
    μHist[1] = μ

    #time 1 onward
    for t in range(1,T)
        c,n,x,xi = time1_allocation(μ)
        s = sHist[t]
        tau = Tau(c[s],n[s])
        uc = 1.0/c[s]
        

        cHist[t+1],nHist[t+1],BHist[t+1],TauHist[t+1] = c[s],n[s],x[s]/uc,tau
        μHist[t+1] = μ
    end 
    
    cHist,nHist,BHist,TauHist,sHist,μHist 
end

simulation (generic function with 2 methods)

In [9]:
time0_allocation(0.45,1)

8.51238919174431
8.853175075816655
8.925674985775371
8.636451449073407
7.942672037234905
6.890160491685874
5.617978205949171
4.312794265766699
3.1378843559868113
2.184860809507835
1.4711067712847414
0.9668090499136422
0.6247163853001622
0.398938907612608
0.25258836360198667
0.15881795616486982
0.09918223959743738
0.061440634958340366
0.03764319084319951
0.02269955909798389
0.013390146358212035
0.007721033249720089
0.004531986875589535
0.0031922730035343822
0.003035887081476366
0.0032717214541338317
0.003519416523875125
0.0036958741346016654
0.0038037614156005233
0.003860915080337084
0.003883588318740078
0.0038837060278615505
0.0038693841179558005
0.0038459617596797225
0.003816890351803081
0.003784379137773514
0.0037498339365354526
0.0037141458920331954
0.0036778782849585974
0.003641386225921901
0.003604892910347787
0.0035685380367315813
0.0035324084896440266
0.0034965577617384405
0.0034610182406947776
0.0034258089797394023
0.0033909406120103598
0.0033564184584028204
0.00332224449309750

2.9855675845232068e-5
2.9557068479589334e-5
2.926144819316821e-5
2.8968785072887824e-5
2.86790495953993e-5
2.8392212373244528e-5
2.8108244479576533e-5
2.7827117168305114e-5
2.7548802023293157e-5
2.7273270908783617e-5
2.700049598669868e-5
2.6730449616927504e-5
2.6463104528362793e-5
2.6198433723745293e-5
2.5936410410269382e-5
2.5677008116692748e-5
2.5420200591767525e-5
2.516596187723391e-5
2.4914266322180067e-5
2.4665088409736585e-5
2.4418402957947865e-5
2.4174185069372197e-5
2.393241005706335e-5
2.3693053410889757e-5
2.3456091014541607e-5
2.3221498859402978e-5
2.29892532287717e-5
2.2759330684519884e-5
2.2531707977798004e-5
2.230636205348359e-5
2.2083270199972323e-5
2.1862409803400424e-5
2.1643758554978165e-5
2.1427294356968816e-5
2.1212995356186964e-5
2.1000839844421064e-5
2.079080641234868e-5
2.0582873780078125e-5
2.0377020991848574e-5
2.0173227202999495e-5
1.99714718260757e-5
1.9771734442949224e-5
1.9573994920291017e-5
1.937823320522637e-5
1.9184429550730768e-5
1.899256434033685e-5
1.

4-element Array{Float64,1}:
 -0.225191
  0.479957
  0.579957
  2.5234  

e-5
1.3631124123966202e-5
1.349480233993596e-5
1.335984398274725e-5
1.3226235414581097e-5
1.3093963132509473e-5
1.2963013759447154e-5
1.2833374071860065e-5
1.2705030984969627e-5
1.2577971491446164e-5
1.2452182797322432e-5
1.2327652165769072e-5
1.2204367007469185e-5
1.2082314887256766e-5
1.1961483428533796e-5
1.1841860501495443e-5
1.1723433927898062e-5
1.1606191770282277e-5
1.1490122222235867e-5
1.137521347481892e-5
1.1261454006666806e-5
1.114883225228212e-5
1.1037336878180528e-5
1.0926956598599897e-5
1.0817680255519867e-5
1.070949679578274e-5
1.060239532272102e-5
1.0496364972453976e-5
1.0391395062051279e-5
1.0287474986959522e-5
1.0184594230820353e-5
1.0082742399279587e-5
9.981909209039193e-6
Converged in 625 steps


In [10]:
##### Model Simulation
mc = MarkovChain(Π, [1, 2])
sHist = simulate(mc,5000,init=1)
#sHist = [1; 1; 1; 1; 1; 1; 1; 1; 2; 2; 1; 1; 1; 2; 2; 2; 2; 2; 2; 1]
sim_seq = simulation(0.85,1,length(sHist),sHist)
sim_seq[1]

35.068498072661896
67.68893919067312
95.90722478247402
848.3179021924878
1594.2071253494628
61.68839259158894
51.4750667755261
43.80387123852015
37.87204173980253
33.17592980421748
29.384987930945716
26.274133117066008
23.68531470163994
21.50462397139466
19.64810991240102
18.052687691330316
16.670138661949796
15.463048337310806
14.401993856536766
13.46355732230607
12.628897213990204
11.882704463013148
11.21242844096151
10.607695433030347
10.059866418829385
9.56169704261608
9.10707347877371
8.690805310843853
8.308461694131656
7.95624070142408
7.63086434090535
7.329493604679085
7.049659270531836
6.789205185378178
6.546241507489861
6.319105946882273
6.106331469084776
5.906619252622076
5.718815940580947
5.541894420323222
5.374937516441941
5.217124100585379
5.067717215351921
4.926053883763834
4.791536335152089
4.663624425894586
4.541829071849495
4.425706540443201
4.314853475703497
4.208902550239387
4.1075186551718605
4.010395553035676
3.9172529302686114
3.8278337955356547
3.741902178162181


0.02734696253407067
0.027089287548234354
0.026833877116525774
0.026580714740126337
0.026329783965660464
0.02608106838616363
0.02583455164253352
0.025590217426545204
0.025348049481906745
0.025108031604804387
0.024870147647441
0.0246343815185346
0.024400717184327216
0.02416913867139152
0.023939630066074937
0.023712175517883932
0.023486759239117635
0.023263365507060377
0.023041978664594003
0.022822583121733526
0.022605163356096723
0.022389703915003046
0.02217618941480976
0.021964604544290174
0.021754934062191825
0.021547162801532963
0.02134127566851821
0.021137257643388516
0.020935093781611035
0.020734769214151662
0.020536269149479345
0.020339578872151223
0.02014468374491021
0.019951569208722982
0.019760220783094824
0.019570624067896204
0.01938276474185301
0.019196628564201693
0.019012201375720527
0.01882946909699345
0.01864841773106139
0.018469033363009573
0.018291302159257672
0.018115210369036943
0.017940744324967128
0.017767890441186308
0.017596635216878275
0.01742696523307736
0.017258

0.0003018669961923438
0.0002988500670491333
0.00029586327232646763
0.0002929063120749442
0.00028997888742492205
0.00028708070528619755
0.0002842114721407566
0.00028137090057831225
0.0002785587039610826
0.00027577459902230355
0.00027301830555921707
0.0002702895465246787
0.0002675880466770855
0.0002649135334330951
0.0002622657388936313
0.00025964439511216256
0.00025704923885392256
0.00025448000874110654
0.0002519364451781479
0.00024941829362120293
0.0002469252981140322
0.0002444572101400876
0.00024201377947513037
0.00023959476013414222
0.00023719990904615094
0.00023482898436294608
0.0002324817477611888
0.00023015796258944813
0.00022785739436946613
0.00022557981268054607
0.0002233249855252987
0.00022109268885309673
0.0002188826950544007
0.00021669478351857762
0.0002145287319510617
0.00021238432407926113
0.00021026134158291806
0.00020815957315347382
0.0002060788043277279
0.00020401882752991927
0.0002019794341735848
0.0001999604190546193
0.0001979615780776888
0.000195982710805563
0.00019402

5001-element Array{Float64,1}:
 0.49846 
 0.415265
 0.415265
 0.360871
 0.360871
 0.415265
 0.360871
 0.415265
 0.415265
 0.415265
 0.415265
 0.415265
 0.360871
 ⋮       
 0.415265
 0.360871
 0.360871
 0.415265
 0.415265
 0.415265
 0.360871
 0.360871
 0.360871
 0.360871
 0.415265
 0.360871

1.1291918487785844e-5
1.117900134167815e-5
1.1067214060812291e-5
1.095654396793793e-5
1.0846981072959514e-5
1.0738513160336308e-5
1.0631130510477226e-5
1.0524821359076052e-5
1.041957510116861e-5
1.0315381693868644e-5
1.0212229500693638e-5
1.0110109630848395e-5
1.0009009963988632e-5
9.908922462828465e-6
Converged in 1277 steps


In [11]:
using Plots

In [12]:
#plot policies
p1 = plot(sim_seq[1],shape = :circle,
    title = "Consumption",legend=false)
p2 = plot(sim_seq[2],shape = :circle,
    title = "Labor",legend=false)
p3 = plot(sim_seq[3],shape = :circle,
    title = "Government Debt",legend=false)
p4 = plot(sim_seq[4],shape = :circle,
    title = "Taxes",legend=false)
p5 = plot(G[sHist],shape = :circle,
    title = "Government Spending",legend=false)
p6 = plot(sim_seq[1],shape = :circle,
    title = "Output",legend=false)
plot(p1,p2,p3,p4,p5,p6,layout = (3,2))